In [1]:
!pip install transformers

    numpy (>=1.19.*) ; python_version >= "3.7"
           ~~~~~~~^

[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip


In [ ]:
from transformers import T5Tokenizer, AutoModelForSeq2SeqLM

# Load the model
model_checkpoint = "midnightGlow/flant5_xlsum_bangla"
trained_model = AutoModelForSeq2SeqLM.from_pretrained(model_checkpoint)

# Load the tokenizer
tokenizer_checkpoint = "midnightGlow/flant5-bangla-tokenizer"
trained_tokenizer = T5Tokenizer.from_pretrained(tokenizer_checkpoint)

# Ensure tokenizer and model compatibility
trained_tokenizer.add_special_tokens({'pad_token': '<pad>'})
trained_model.resize_token_embeddings(len(trained_tokenizer))

print("Model and tokenizer successfully loaded with custom Bangla vocabulary.")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.55k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/308M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/142 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/20.9k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/1.17M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/2.61k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.82k [00:00<?, ?B/s]

Model and tokenizer successfully loaded with custom Bangla vocabulary.


In [ ]:
trained_model.resize_token_embeddings(len(trained_tokenizer))

Embedding(32101, 512)

In [ ]:
import pandas as pd

# Load the custom dataset
text_sum_dataset = pd.read_csv('/content/textsum_balanced.csv')

# Ensure it has the expected columns
text_sum_dataset.head()

category                                            summary  \
0    state  বর্তমান মেয়াদে গ্রামীণ ব্যাংক নিয়ে নতুন পরিক...   
1    state  স্বাস্থ্য বাতায়ন ১৬২৬৩ উন্নয়নের লক্ষ্যে জনগণের...   
2    state  পর্যটন বর্ষ পালন উপলক্ষে কুয়াকাটায় পরিচ্ছন্নতা...   
3    state  আ.লীগ মুক্তিযোদ্ধার দল নয় জিয়া দেশের প্রথম রাষ...   
4    state  ব্যাংকের করপোরেট কর কমানোর প্রস্তাবে সংসদে অর্...   

                                                text  
0  বাকি মেয়াদে গ্রামীণ ব্যাংক নিয়ে নতুন কোনো পর...  
1  ২৬ ডিসেম্বর ২০১৬, প্রথম আলোর আয়োজনে ‘স্বাস্থ...  
2  ‘আমরা গড়ব আমার দেশ, পর্যটকবান্ধব পরিবেশ’ স্লোগ...  
3  জিয়াউর রহমানই দেশের প্রথম রাষ্ট্রপতি বলে দাবি ...  
4  ব্যাংক খাতে লুটপাটের মধ্যে ব্যাংক ও আর্থিক প্র...

In [ ]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 23.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.0 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:
def preprocess_function(examples):
    inputs = [text for text in examples['text']]
    targets = [summary for summary in examples['summary']]
    model_inputs = trained_tokenizer(inputs, max_length=512, truncation=True)

    # Set up the tokenizer for targets
    with trained_tokenizer.as_target_tokenizer():
        labels = trained_tokenizer(targets, max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

from datasets import Dataset

# Convert the DataFrame to Hugging Face Dataset
dataset = Dataset.from_pandas(text_sum_dataset)

# Tokenize the dataset
tokenized_dataset = dataset.map(preprocess_function, batched=True)
tokenized_dataset = tokenized_dataset.train_test_split(test_size=0.1)
train_dataset = tokenized_dataset['train']
val_dataset = tokenized_dataset['test']


NameError: name 'text_sum_dataset' is not defined

In [ ]:
from transformers import DataCollatorForSeq2Seq

# Define the data collator
data_collator = DataCollatorForSeq2Seq(
    tokenizer=trained_tokenizer,
    model=trained_model,
    padding=True,
    max_length=512,  # Max length for input sequences
    label_pad_token_id=-100,  # Label pad token id
)

In [ ]:
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir='./results_bangla_custom',
    evaluation_strategy="epoch",
    learning_rate=5e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=5,
    predict_with_generate=True,
    logging_steps=100,
    save_steps=500,
    save_strategy="epoch",
    push_to_hub=False,

)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
trainer = Seq2SeqTrainer(
    model=trained_model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=trained_tokenizer,
    data_collator=data_collator,
)

<ipython-input-11-83579d69e43f>:1: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer = Seq2SeqTrainer(


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
print(train_dataset[:5])
print(val_dataset[:5])

{'category': ['state', 'international', 'sports', 'international', 'sports'], 'summary': ['আহমদ ছফা সারা জীবন আপন সমাজের কথা ভেবেছেন', 'আগরতলায় ৬০ ফুট দুর্গা, আছে হাজার হাতও', 'শাওলিন সকারের অবিশ্বাস্য গোল করে দেখালেন ইব্রা', 'চীনে কয়লা খনিতে আগুন , নিহত ২১', 'ইংলিশ প্রিমিয়ার লিগকেও পানসে বানিয়ে ফেললেন তিনি!'], 'text': ['আহমদ ছফা স্বপ্ন দেখেছিলেন, বাংলাদেশের গণসংগ্রামের উত্তাপ থেকে নতুন মানুষ জন্ম নেবে। তাঁর বিশ্বাস ছিল, অন্তরের অমৃত বলে বুক বেঁধে আবার দাঁড়াবে বাংলাদেশ। গতকাল শুক্রবার সকালে ‘আহমদ ছফার সাধনা’ শীর্ষক বক্তৃতায় ছাত্র ফেডারেশনের ঢাকা বিশ্ববিদ্যালয় শাখার সাবেক সভাপতি আফজালুর রহমান এসব কথা বলেন। আহমদ ছফার ১২তম মৃত্যুবার্ষিকী উপলক্ষে আহমদ ছফা রাষ্ট্রসভা ঢাকা বিশ্ববিদ্যালয়ের বাণিজ্য অনুষদের সম্মেলনকক্ষে এ ১১তম স্মৃতি বক্তৃতার আয়োজন করে।\xa0স্মৃতি বক্তৃতায় আফজালুর রহমান বলেন, আহমদ ছফার সারা জীবনের লক্ষ্য ছিল আপন সমাজের মানুষকে ন্যায়নীতি, বিজ্ঞানদৃষ্টি, মানবিকতা ও অসাম্প্রদায়িকতার দিকে চালিত করা। সভাপতির বক্তব্যে মুহম্মদ নুরুল ইসলাম বলেন, শিক্ষার প্রধান লক্ষ্য হওয়া উচিত 

In [ ]:
for example in train_dataset:
    print(example['input_ids'])  # Ensure they are not empty
    print(example['labels'])


Streaming output truncated to the last 5000 lines.
[1334, 15493, 998, 24, 349, 31945, 23274, 3432, 2991, 7199, 4186, 7, 574, 11749, 1008, 884, 2703, 1942, 1023, 10782, 4435, 1084, 882, 715, 24688, 14610, 31948, 227, 187, 193, 141, 4280, 123, 2675, 4771, 678, 882, 31948, 3246, 7199, 4186, 7, 8510, 16102, 1028, 2498, 832, 31965, 1013, 2125, 246, 556, 1925, 14692, 31948, 15943, 7199, 4186, 7, 3251, 1181, 1997, 1715, 7701, 391, 31948, 7199, 4186, 7, 1367, 8238, 6446, 377, 1334, 1957, 3478, 24, 349, 31945, 23274, 3414, 2703, 612, 99, 31965, 1328, 31059, 28081, 11749, 16797, 5462, 1715, 7199, 4186, 7, 3251, 3998, 31948, 227, 211, 123, 18792, 24405, 31965, 123, 9789, 31965, 123, 1206, 31965, 1997, 31924, 0, 790, 37, 3998, 31948, 31924, 0, 14192, 1997, 1715, 19946, 4404, 3624, 89, 1042, 293, 4359, 10847, 31948, 1057, 840, 3820, 15124, 101, 1424, 47, 2326, 612, 156, 31965, 7199, 4186, 26, 8816, 884, 996, 2675, 3006, 293, 345, 7879, 489, 3819, 3332, 1405, 292, 31948, 141, 4280, 10672, 982, 5097,

In [ ]:
print(trained_tokenizer.special_tokens_map)

{'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'sep_token': '</s>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<extra_id_40>', '<extra_id_41>', '<extra_id_42>', '<extra_id_43>', '<extra_id_44>', '<extra_id_45>', '<extra_id_46>', '<extra_id_47>', '<extra_id_48>', '<extra_id_49>', '<extra_id_50>', '<extr

In [ ]:
# Start fine-tuning
trainer.train()

# Save the fine-tuned model and tokenizer
trainer.save_model('/content/drive/MyDrive/Source_Domain_flant5_bangla_model')
trained_tokenizer.save_pretrained('/content/drive/MyDrive/Source_Domain__flant5_bangla_tokenizer')

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.48.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/usr

('/content/drive/MyDrive/Source_Domain__flant5_bangla_tokenizer/tokenizer_config.json',
 '/content/drive/MyDrive/Source_Domain__flant5_bangla_tokenizer/special_tokens_map.json',
 '/content/drive/MyDrive/Source_Domain__flant5_bangla_tokenizer/spiece.model',
 '/content/drive/MyDrive/Source_Domain__flant5_bangla_tokenizer/added_tokens.json')

In [2]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

# Path to the saved model and tokenizer
model_path = "midnightGlow/flant5-xlsum-bangla-source-domain"
tokenizer_path = "midnightGlow/flant5-bangla-tokenizer"

# Load the trained model
model = AutoModelForSeq2SeqLM.from_pretrained(model_path)

# Load the trained tokenizer
tokenizer = AutoTokenizer.from_pretrained(tokenizer_path)

# Ensure tokenizer and model compatibility
tokenizer.add_special_tokens({'pad_token': '<pad>'})
model.resize_token_embeddings(len(tokenizer))

print("Model and tokenizer successfully loaded")



/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
You set `add_prefix_space`. The tokenizer needs to be converted from the slow tokenizers


Model and tokenizer successfully loaded


In [ ]:
!pip install datasets evaluate nltk sacrebleu rouge_score rouge

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.8/51.8 kB 4.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 26.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.0/104.0 kB 9.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 16.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.1 MB/s eta 0:00:00
  Created wheel for rouge_score: filename=rouge_score-0.1.2-py3-none-any.whl size=24935 sha256=230358755c34dbff1ff15c2e99baddd70193403c1f7379d70e814cd736686d21
  Stored in directory: /root/.cache/pip/wheels/5f/dd/89/461065a73be61a532ff8599a28e9beef17985c9e9c31e541b4
Successfully built rouge_score
  Attempting unins

In [ ]:
import evaluate
# Load ROUGE metric
rouge = evaluate.load("rouge")

In [ ]:
# Select a small batch (e.g., first 5 examples from the validation dataset)
batch = val_dataset.select(range(5))

In [ ]:
def generate_predictions_and_calculate_rouge(model, tokenizer, batch):
    inputs = tokenizer(
        [example["text"] for example in batch],
        return_tensors="pt",
        padding=True,
        truncation=True,
        max_length=512
    )

    # Generate summaries
    outputs = model.generate(inputs.input_ids, max_length=128, num_beams=4, early_stopping=True)

    # Decode the summaries
    generated_summaries = tokenizer.batch_decode(outputs, skip_special_tokens=True)
    reference_summaries = [example["summary"] for example in batch]

    # Calculate ROUGE score
    rouge_score = rouge.compute(predictions=generated_summaries, references=reference_summaries)

    return generated_summaries, reference_summaries, rouge_score


In [ ]:
# Generate predictions and ROUGE score
generated_summaries, reference_summaries, rouge_score = generate_predictions_and_calculate_rouge(model, tokenizer, batch)

# Print the results
print("Generated Summaries:")
for i, summary in enumerate(generated_summaries):
    print(f"Example {i+1}: {summary}")

print("\nReference Summaries:")
for i, ref_summary in enumerate(reference_summaries):
    print(f"Example {i+1}: {ref_summary}")

print("\nROUGE Score:", rouge_score)

Generated Summaries:
Example 1: কানাডার কুইবেক সিটির মসজিদে হামলা চালিয়েছে সন্ত্রাসীরা
Example 2: ব্রাজিল-মেক্সিকো খেলা দেখা নিয়ে সংঘর্ষে আহত
Example 3: বাংলাদেশ টেস্ট অধিনায়কের?:থামের জন্মদিন
Example 4: এক মন্ত্রীর মেয়ের বিয়েতে ৫০০
Example 5:  মার্কিন                                                                                                                      

Reference Summaries:
Example 1: কানাডায় মসজিদে ঢুকে গুলি, ছয় মুসল্লি নিহত
Example 2: নেত্রকোনায় ব্রাজিল-মেক্সিকো খেলা দেখা নিয়ে সংঘর্ষ, নিহত ১
Example 3: কিংবদন্তি বোথামের জন্মদিনে তাঁরই রেকর্ড সাকিবের মুকুটে
Example 4: মেয়ের বিয়েতে ৯০ গৃহহীনকে ঘর দিলেন ধনাঢ্য ব্যবসায়ী
Example 5: ‘বিএনপি নির্বাচন নিয়ে একেক সময় একেক কথা বলে’

ROUGE Score: {'rouge1': 0.0, 'rouge2': 0.0, 'rougeL': 0.0, 'rougeLsum': 0.0}


In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: write).
The token `train model` has been saved to /root/.cache/huggingface/stored_tokens
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate wh

In [81]:
model.resize_token_embeddings(len(tokenizer))

Embedding(32101, 512)

In [82]:
import pandas as pd
from datasets import Dataset

# Example: load your datasets (ensure they have 'text' and 'summary' columns)
state_dataset = pd.read_csv("/content/state_categories.csv")
international_dataset = pd.read_csv("/content/international_categories.csv")
sports_dataset = pd.read_csv("/content/sports_categories.csv")

# Convert to Hugging Face Dataset
state_dataset = Dataset.from_pandas(state_dataset)
international_dataset = Dataset.from_pandas(international_dataset)
sports_dataset = Dataset.from_pandas(sports_dataset)


In [ ]:
state_dataset.to_pandas().head()

category                                              title  \
0    state     ভোট কেন্দ্রে ক্রিকেট খেলছিলেন পুলিশ কর্মকর্তা!   
1    state               এ কেমন শহর, আট মাসে দুবার ডেঙ্গু হয়!   
2    state           যেখানে ‘দাপট’ দেখাতে পারছে না আওয়ামী লীগ   
3    state  প্রধানমন্ত্রী অনুরোধ করলে ‘না’ করতে পারব না: অ...   
4    state      সাবেক বিমান প্রতিমন্ত্রী মাহবুব আলী গ্রেপ্তার   

                                                text  \
0  ঠাকুরগাঁও-৩ আসনের উপনির্বাচনে কোনো উত্তাপ ছিল ...   
1  চট্টগ্রাম মেডিকেল কলেজ হাসপাতালের মেডিসিন ওয়ার...   
2  রাজপথে শক্তির ‘প্রদর্শন’ কিংবা নির্বাচনী কৌশল—...   
3  অর্থমন্ত্রী আবুল মাল আবদুল মুহিত বলেছেন, প্রধা...   
4  সাবেক বেসামরিক বিমান পরিবহন ও পর্যটন প্রতিমন্ত...   

                                             summary  
0  ঠাকুরগাঁও-৩ আসনের উপনির্বাচনে কোনো উত্তাপ ছিল ...  
1  চট্টগ্রাম মেডিকেল কলেজ হাসপাতালের মেডিসিন ওয়ার...  
2  রাজপথে শক্তির ‘প্রদর্শন’ কিংবা নির্বাচনী কৌশল—...  
3  অর্থমন্ত্রী আবুল মাল আবদুল মুহিত বলেছেন, প্রধা...  
4  সাবেক বেসামরিক বিমান পরিবহন ও পর্যটন প্রতিমন্ত...

In [ ]:
international_dataset.to_pandas().head()

category                                              title  \
0  international    ব্রিটিশ এম্পায়ার মেডেল পেলেন রেহানা খানম রহমান   
1  international  কুয়ালালামপুরে মিয়ানমার ও বাংলাদেশিদের ১৮ প্রতি...   
2  international  মালয়েশিয়ায় ট্রেনের ধাক্কায় নিহত ২ বাংলাদেশির প...   
3  international  ঢাকা-আবুধাবি রুটে বন্ধ হচ্ছে ইতিহাদ এয়ারওয়েজের...   
4  international    ২০২৩ সালে দেশে এসেছে রেকর্ড ৪৫৫২ প্রবাসীর মরদেহ   

                                                text  \
0  ব্রিটেনের রাজ পরিবারের দেওয়া 'মেডেল অব দ্য অর্...   
1  মালয়েশিয়ায় বাংলাদেশ ও মিয়ানমারের নাগরিকদের পরি...   
2  মালয়েশিয়ায় ট্রেনের ধাক্কায় নিহত তিন বাংলাদেশির...   
3  সংযুক্ত আরব আমিরাতের রাজধানী আবুধাবি থেকে ঢাকা...   
4  পরিবারের দারিদ্র ঘোচাতে ২০১৯ সালে শ্রমিক হিসেব...   

                                             summary  
0  ব্রিটেনের রাজ পরিবারের দেওয়া 'মেডেল অব দ্য অর্...  
1  মালয়েশিয়ায় বাংলাদেশ ও মিয়ানমারের নাগরিকদের পরি...  
2  মালয়েশিয়ায় ট্রেনের ধাক্কায় নিহত তিন বাংলাদ...  
3  সংযুক্ত আরব আমিরাতের রাজধানী আবুধাবি থেকে ঢাকা...  
4  পরিবারের দারিদ্র ঘোচাতে ২০১৯ সালে শ্রমিক হিসেব...

In [ ]:
sports_dataset.to_pandas().head()

category                                              title  \
0   sports  ইউরোপিয়ান সুপার লিগ: 'ফ্যান পাওয়ার' যেভাবে ব...   
1   sports                                 ধুঁকছে মাশরাফির দল   
2   sports  সোহাগের ওপর ফিফার নিষেধাজ্ঞা: বাংলাদেশের ফুটবল...   
3   sports  কনফারেন্স লিগের সেমির প্রথম লেগে নিষিদ্ধ মার্ত...   
4   sports  ইএসএল: বার্সেলোনা, রেয়াল মাদ্রিদ, লিভারপুল, ম...   

                                                text  \
0  ফুটবলে একটিও কিক না মেরেই শেষ হয়ে গেল একটি লি...   
1  সব শংকা উড়িয়ে মাঠে গড়িয়েছে বাংলাদেশ প্রিমিয়ার ...   
2  শুক্রবার ১৪ই এপ্রিল ফিফার ওয়েবসাইটে প্রকাশিত এ...   
3  নিয়মের ফাঁক দিয়ে দুটি হলুদ কার্ড পেয়েও লাল কার...   
4  ইংল্যান্ডের 'বিগ সিক্স' বলে পরিচিত আর্সেনাল, চ...   

                                             summary  
0   ফুটবলে একটিও কিক না মেরেই শেষ হয়ে গেল একটি লিগ।  
1  সব শংকা উড়িয়ে মাঠে গড়িয়েছে বাংলাদেশ প্রিমিয়ার ...  
2  বাংলাদেশের ফুটবল ফেডারেশনের সাধারণ সম্পাদক আবু...  
3  অলিম্পিয়াকোসের বিপক্ষে প্রথম লেগে আর্জেন্টিনার...  
4  ইংল্যান্ডের 'বিগ সিক্স' বলে পরিচিত আর্সেনাল, চ...

In [83]:
def preprocess_function(examples):
    inputs = [text for text in examples['text']]
    targets = [summary for summary in examples['summary']]
    model_inputs = tokenizer(inputs, max_length=512, truncation=True, padding=True)

    # Set up the tokenizer for targets
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(targets, max_length=128, truncation=True, padding=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

# Tokenize each dataset
state_tokenized = state_dataset.map(preprocess_function, batched=True)
international_tokenized = international_dataset.map(preprocess_function, batched=True)
sports_tokenized = sports_dataset.map(preprocess_function, batched=True)

# Now, split each dataset into train, validation, and test sets
# Example: 80% train, 10% validation, 10% test split
state_split = state_tokenized.train_test_split(test_size=0.2)  # 80% train, 20% test
state_train = state_split['train']
state_test = state_split['test']

# Split the test set further into validation and test sets (50-50 split)
state_val_test_split = state_test.train_test_split(test_size=0.5)
state_val = state_val_test_split['train']
state_test = state_val_test_split['test']

# Repeat for the international and sports datasets
international_split = international_tokenized.train_test_split(test_size=0.2)  # 80% train, 20% test
international_train = international_split['train']
international_test = international_split['test']

# Split the test set further into validation and test sets (50-50 split)
international_val_test_split = international_test.train_test_split(test_size=0.5)
international_val = international_val_test_split['train']
international_test = international_val_test_split['test']

sports_split = sports_tokenized.train_test_split(test_size=0.2)  # 80% train, 20% test
sports_train = sports_split['train']
sports_test = sports_split['test']

# Split the test set further into validation and test sets (50-50 split)
sports_val_test_split = sports_test.train_test_split(test_size=0.5)
sports_val = sports_val_test_split['train']
sports_test = sports_val_test_split['test']


Map:   0%|          | 0/4989 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4114: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


Map:   0%|          | 0/4158 [00:00<?, ? examples/s]

Map:   0%|          | 0/2494 [00:00<?, ? examples/s]

In [84]:
from transformers import DataCollatorForSeq2Seq

# Define the data collator
data_collator2 = DataCollatorForSeq2Seq(
    tokenizer=tokenizer,
    model=model,
    padding=True,
    max_length=512,  # Max length for input sequences
    label_pad_token_id=-100,  # Label pad token id
)

In [ ]:
 !pip install datasets transformers[sentencepiece]

In [85]:
from transformers import Seq2SeqTrainingArguments, Seq2SeqTrainer
import pandas as pd
# Set up training arguments
training_args2 = Seq2SeqTrainingArguments(
    output_dir="./domain_fine_tuned_models",
    evaluation_strategy="epoch",
    learning_rate=1e-5,
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=10,
    predict_with_generate=True,
    logging_steps=100,
    save_steps=500,
    save_strategy="epoch",
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [86]:
from transformers import TrainingArguments, AutoTokenizer, AutoModelForSeq2SeqLM, Trainer
trainer_state = Seq2SeqTrainer(
    model=model,
    args=training_args2,
    train_dataset=state_train,  # Replace with your dataset
    eval_dataset=state_val,  # Replace with your dataset
    tokenizer=tokenizer,
    data_collator=data_collator2,
    #compute_metrics=compute_metrics,  # Pass the custom compute_metrics function
)

<ipython-input-86-74d87a5376f3>:2: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer_state = Seq2SeqTrainer(


In [87]:
# Fine-tune on each domain
trainer_state.train()
trainer_state.save_model("/content/drive/MyDrive/state_domain_model")
tokenizer.save_pretrained("/content/drive/MyDrive/state_domain_tokenizer")

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:2852: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(


KeyboardInterrupt: 

In [68]:
!pip install torch

In [ ]:
test_text = "হিন্দু বাঙালীরা যে সময়ে তাদের সবথেকে বড় উৎসব দুর্গাপূজা উদযাপন করেন, সেই সময়েই শোক পালন করেন অসুর বংশীয় আদিবাসীরা।"
encoded = tokenizer(test_text, return_tensors="pt")
decoded = tokenizer.decode(encoded["input_ids"][0])
print("Encoded:", encoded)
print("Decoded:", decoded)


Encoded: {'input_ids': tensor([[ 1455, 27267,   109,  1396,   213, 12379,   578,  2905, 21701,  6101,
           420, 31965,   495,  8930,  7116,  2078,   420,   971,    71,  4739,
           145, 27567, 31948,     2]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}
Decoded: হিন্দু বাঙালীরা যে সময়ে তাদের সবথেকে বড় উৎসব দুর্গাপূজা উদযাপন করেন, সেই সময়েই শোক পালন করেন অসুর বংশীয় আদিবাসীরা।</s>


In [71]:
import torch
for param in model.parameters():
    if torch.isnan(param.grad).any():
        print("Gradient contains NaN!")


Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient contains NaN!
Gradient co

In [73]:
print(tokenizer.special_tokens_map)


{'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'sep_token': '</s>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<extra_id_40>', '<extra_id_41>', '<extra_id_42>', '<extra_id_43>', '<extra_id_44>', '<extra_id_45>', '<extra_id_46>', '<extra_id_47>', '<extra_id_48>', '<extra_id_49>', '<extra_id_50>', '<extr

In [74]:
torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)


tensor(nan, device='cuda:0')

In [78]:
for example in state_train:
    with torch.no_grad():
        # Extract input_ids, attention_mask, and labels from the example
        input_ids = example["input_ids"]
        attention_mask = example["attention_mask"]
        labels = example["labels"]

        print("Input IDs:", input_ids)
        print("Attention Mask:", attention_mask)
        print("Labels:", labels)
        outputs = model(input_ids, attention_mask=attention_mask, labels=labels)
        print("Logits:", outputs.logits)
        print("Loss:", outputs.loss)

Input IDs: [203, 3633, 645, 385, 448, 3706, 1093, 715, 838, 1757, 3210, 367, 2817, 697, 75, 12158, 822, 31965, 8179, 3, 128, 5505, 14991, 78, 54, 715, 5131, 128, 174, 5933, 1969, 1210, 31948, 9119, 218, 1466, 838, 1757, 31965, 2059, 7707, 1362, 101, 3210, 1762, 218, 3706, 889, 31948, 1216, 650, 31987, 4965, 31998, 6293, 396, 31955, 11, 30, 994, 1626, 5554, 838, 13568, 26, 148, 18199, 53, 746, 1849, 1256, 31948, 115, 418, 203, 1089, 8874, 47, 3680, 128, 10149, 4747, 923, 6943, 226, 31948, 838, 1757, 2268, 742, 715, 1210, 13220, 634, 31965, 828, 1292, 2157, 1387, 24969, 54, 3706, 1570, 2128, 31948, 94, 455, 8976, 333, 546, 12146, 2415, 23480, 1930, 128, 4805, 4289, 3222, 4692, 187, 13829, 1210, 193, 31948, 483, 7418, 774, 1097, 1726, 489, 5936, 1210, 31948, 7707, 634, 193, 859, 3706, 2396, 31965, 949, 0, 14975, 14094, 901, 8401, 2267, 1097, 2775, 3995, 2807, 198, 31948, 838, 3704, 13860, 203, 3227, 5490, 6159, 365, 31948, 7707, 1362, 101, 588, 3643, 1357, 10269, 18553, 198, 4115, 31948, 

AttributeError: 'list' object has no attribute 'size'

In [ ]:
print(state_train[0])  # Inspect a training sample


{'category': 'state', 'title': 'শেখ হাসিনা: গণতন্ত্রের প্রতীক থেকে যেভাবে ‘স্বৈরাচার’', 'text': 'বাংলাদেশের ইতিহাসে সবচেয়ে বেশি দিন ক্ষমতায় থাকা প্রধানমন্ত্রী শেখ হাসিনা টানা কয়েক সপ্তাহের ছাত্র ও জনতার বিক্ষোভ, রক্তক্ষয় এবং দেশজুড়ে অশান্তির পর প্রধানমন্ত্রীপদ এবং দেশ ছাড়তে বাধ্য হন। ৭৬ বছর বয়সী শেখ হাসিনা, যিনি ২০০৯ সাল থেকে টানা ১৬ বছর ক্ষমতায় ছিলেন। সোমবার (৫ আগস্ট) জনগণের রোষানলে পড়ে ছোট বোন শেখ রেহানাকে নিয়ে হেলিকপ্টারে করে ভারতে পালিয়ে যান। এই ঘটনা বাংলাদেশের রাজনৈতিক অঙ্গনে এক বিরল এবং অবিশ্বাস্য অধ্যায়ের সূচনা করেছে।\nশেখ হাসিনা প্রথমবারের মতো প্রধানমন্ত্রী হন ১৯৯৬ সালে, যখন আওয়ামী লীগ দীর্ঘ বিরতির পর ক্ষমতায় ফিরে আসে। তার প্রথম মেয়াদে ভারতের সঙ্গে গঙ্গা পানি বণ্টন চুক্তি এবং পার্বত্য চট্টগ্রামে শান্তি চুক্তির জন্য প্রশংসিত হন তিনি। তবে ২০০১ সালের নির্বাচনে বিএনপির কাছে পরাজিত হন। ২০০৯ সালে তিনি আবার ক্ষমতায় আসেন, সেনা–সমর্থিত তত্ত্বাবধায়ক সরকারের অধীনে অনুষ্ঠিত নির্বাচনে বিপুল ভোটে বিজয়ী হয়ে।\nশেখ হাসিনার শাসনামলে বাংলাদেশের অর্থনৈতিক অগ্রগতি উল্লেখযোগ্য ছিল। ২০০৯ সাল থেকে দে

In [76]:
for example in state_train:
    print(f"Input: {example['input_ids']}")
    print(f"Label: {example['labels']}")
    break


Input: [203, 3633, 645, 385, 448, 3706, 1093, 715, 838, 1757, 3210, 367, 2817, 697, 75, 12158, 822, 31965, 8179, 3, 128, 5505, 14991, 78, 54, 715, 5131, 128, 174, 5933, 1969, 1210, 31948, 9119, 218, 1466, 838, 1757, 31965, 2059, 7707, 1362, 101, 3210, 1762, 218, 3706, 889, 31948, 1216, 650, 31987, 4965, 31998, 6293, 396, 31955, 11, 30, 994, 1626, 5554, 838, 13568, 26, 148, 18199, 53, 746, 1849, 1256, 31948, 115, 418, 203, 1089, 8874, 47, 3680, 128, 10149, 4747, 923, 6943, 226, 31948, 838, 1757, 2268, 742, 715, 1210, 13220, 634, 31965, 828, 1292, 2157, 1387, 24969, 54, 3706, 1570, 2128, 31948, 94, 455, 8976, 333, 546, 12146, 2415, 23480, 1930, 128, 4805, 4289, 3222, 4692, 187, 13829, 1210, 193, 31948, 483, 7418, 774, 1097, 1726, 489, 5936, 1210, 31948, 7707, 634, 193, 859, 3706, 2396, 31965, 949, 0, 14975, 14094, 901, 8401, 2267, 1097, 2775, 3995, 2807, 198, 31948, 838, 3704, 13860, 203, 3227, 5490, 6159, 365, 31948, 7707, 1362, 101, 588, 3643, 1357, 10269, 18553, 198, 4115, 31948, 2372

In [ ]:
print(f"Train size: {len(state_train)}, Validation size: {len(state_val)}, Test size: {len(state_test)}")


Train size: 3991, Validation size: 499, Test size: 499
